In [1]:
"""
Nasa Sherlock data is not very clean by default, this notebook takes as input the Sherlock data and proccess it into 
clean dataframes of individual flights
"""

'\nNasa Sherlock data is not very clean by default, this notebook takes as input the Sherlock data and proccess it into \nclean dataframes of individual flights\n'

In [1]:
import collections
from pathlib import Path
import copy
import os
import pandas as pd
import gzip
import shutil
import glob

# import dask
# import dask.dataframe as dd


from collections import defaultdict
from tqdm import tqdm

import numpy as np
from matplotlib import pyplot as plt

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data as data
from torch.utils.data import DataLoader

import pytorch_lightning as pl
from pytorch_lightning.callbacks import ModelCheckpoint
from lightning.pytorch.loggers import TensorBoardLogger
from pytorch_lightning import loggers
from pytorch_lightning import LightningModule
from pytorch_lightning import Trainer

import random

import matplotlib.pyplot as plt
import matplotlib.image as mpimg

import folium


from pathlib import Path

In [8]:
# # Group by 'key' and then by 'id'
# grouped_by_key = df.groupby('key')
# result = {key: {id: group for id, group in key_group.groupby('id')} for key, key_group in grouped_by_key}

# UAID | CID

def create_dictionary_of_flight_dataframes(csv_paths_list):
    csv_paths_list = csv_paths_list
    dataframes = []
    for idx, csv_path in enumerate(csv_paths_list):
        print(f"working on reading in {csv_path} | {idx + 1} / {len(csv_paths_list)}")
        dataframes.append(pd.read_csv(csv_path))

    dataframes = pd.concat(dataframes, axis=0, ignore_index=True)
    print(f"combined dataframe has shape: {dataframes.shape}")

    grouped = dataframes.groupby('fltKey')
    #flight_dfs = {fltKey: group.sort_values(by=['Time'], ascending=True) for fltKey, group in grouped}
    flight_dfs = {key: {id: group for id, group in key_group.groupby('fltKey')} for key, key_group in grouped}
    return flight_dfs


In [9]:
# dir_clean_iff = "/Users/aleksandranikevich/Desktop/AircraftTrajectory/data/data_clean_iff/"
dir_clean_iff = "/home/ashourm/F2/cleaned/"
iff_csvs_path_list = glob.glob(dir_clean_iff + "*.csv")

flight_dfs = create_dictionary_of_flight_dataframes(iff_csvs_path_list)

working on reading in /home/ashourm/F2/cleaned/F2.csv | 1 / 1
combined dataframe has shape: (47236361, 9)


In [7]:
for key_flight, dict_flight in flight_dfs.items():
    for key_id, dict_id in dict_flight.items():
        print(key_flight, key_id)

34088 2021
34104 1751
34115 4262
34212 0450
34235 0353
34278 DAZ10
34307 1326
35332 N524AG
35391 SKW3847
35405 DAL660
35410 FFT4996
35420 UCM656
35483 ACA573
35578 BAW29C
35630 KLM168
35716 ASA53
35739 DAL2153
35748 DAL1663
35761 TAP226
35794 UPS787
35802 UPS789
35804 OPS7
35810 UPS313
35820 EJM606
35824 UPS771
35828 SWA5357
35834 WJA2661
35840 ROU1647
35841 0327
35842 X304PT
35854 0327
35873 0063
35909 UPS793
35916 2206
35918 1337
35919 0531
35928 0572
35931 0313
35934 LPE2699
35952 FFT1445
35955 SKW5250
36008 AJT1020
36009 1032
36015 SCX3047
36016 UAL605
36017 UAL1396
36018 OAE2167
36020 N9150D
36021 ASA97
36023 6334
36039 0353
36064 4733
36065 DAL910
36075 4301
36076 1344
36081 AAST1
36084 0325
36086 2167
36089 HAL396
36090 6332
36091 SWA2039
36092 FDY954
36093 0405
36094 1032
36097 UAL1266
36098 AFR025
36099 0510
36100 SWA1150
36101 7712
36103 OUA3
36104 JBU636
36105 JBU1289
36106 FFT3938
36107 O04
36108 O91
36109 VIR108B
36110 ST4
36111 0401
36112 OPS39
36113 SWA2786
36114 HAL523


IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [8]:
# Now let's save ever individual flight as it's own dataframe

In [10]:
flight_dfs[35748]['DAL1663']

fltKey    CID     UAID        Time  Latitude  Longitude  Altitude  \
122951806   35748  863.0  DAL1663  1716004930  44.88217  -93.21470      8.31   
122951807   35748  863.0  DAL1663  1716004933  44.88216  -93.21472      8.31   
122951808   35748  863.0  DAL1663  1716004955  44.88196  -93.21501      8.31   
122951809   35748  863.0  DAL1663  1716004956  44.88186  -93.21505      8.31   
122951810   35748  863.0  DAL1663  1716004957  44.88183  -93.21506      8.31   
...           ...    ...      ...         ...       ...        ...       ...   
122952597   35748  863.0  DAL1663  1716008806  49.78500  -97.37194     79.00   
122952598   35748  863.0  DAL1663  1716008818  49.79944  -97.38222     75.00   
122952599   35748  863.0  DAL1663  1716008830  49.81361  -97.39222     69.00   
122952600   35748  863.0  DAL1663  1716008842  49.82778  -97.40222     65.00   
122952601   35748  863.0  DAL1663  1716008854  49.84222  -97.41250     61.00   

          PointSource  RecTypeCat  Significance  GroundSpeed  FlightCourse  
122951806       0xE02           1             7            1           235  
122951807       0xE02           1             8            1           235  
122951808       0xE02           1             1            3           226  
122951809       0xE02           1             6           22           196  
122951810       0xE02           1             1            7           193  
...               ...         ...           ...          ...           ...  
122952597     TH_FIXM           1             4          283           336  
122952598     TH_FIXM           1             8          289           335  
122952599     TH_FIXM           1             4          283           336  
122952600     TH_FIXM           1             8          283           336  
122952601     TH_FIXM           1             1          289           335  

[796 rows x 12 columns]

In [10]:
# individual_flights_dir = "/Users/aleksandranikevich/Desktop/AircraftTrajectory/data/Individual_Flights/"
individual_flights_dir = "/home/ashourm/F2/FS/"


In [ ]:
# from pathlib import Path
# Path("/my/directory").mkdir(parents=True, exist_ok=True)



In [11]:
from tqdm import tqdm

for key_flight, dict_flight in tqdm(flight_dfs.items()):
    key_flight = str(key_flight)
    dir_flight = individual_flights_dir + key_flight + "/"
    Path(dir_flight).mkdir(parents=True, exist_ok=True)
    for key_id, dataframe in dict_flight.items():
        key_id = str(key_id)
        key_dir = dir_flight + key_id + "/"
        Path(key_dir).mkdir(parents=True, exist_ok=True)
        
        csv_name = key_flight + "_" + key_id + ".csv"
        dataframe.to_csv(key_dir + csv_name)


        
        

100%|██████████| 62486/62486 [04:00<00:00, 259.75it/s]
